In [824]:
import sys
sys.path.append('../../')
import pandas as pd
import requests
import plotly.graph_objects as go
import plotly.express as px
from statsmodels.tsa.stattools import adfuller
from numpy import cumsum, log, polyfit, sqrt, std, subtract
import functions.functions as base_fx
import functions.portfolio_functions as portfolio_fx
import functions.pair_portfolio_functions as pairs_portfolio_fx
import functions.mean_algos as algos
import importlib
from binance.client import Client,BinanceAPIException
import json
import math

In [1147]:
symbols = ['XRPBTC']# ['ETHBTC', 'XRPBTC', 'XLMBTC', 'EOSBTC']


In [1148]:
quotes = pd.DataFrame()
#start = '2011-06-1' ## Starts with non-correlated period (drops 40% at the start)
start = '2010-01-1'
end = '2020-05-25'
client = Client('NEI4wgKwWXw8uEjqyHPuBKFgKPgv4xPdpeey2Z17Aek8YWyaOHTsEEAUWPVyl4WH', 'UCw65kdS9N4GkJt2WpQTYgFkXPB6rMkM1ETQARfIbBHL1836Q5oX08IuAUWzFNbD')
for s in symbols:
    print(s)
    klines = client.get_historical_klines(s, Client.KLINE_INTERVAL_30MINUTE, "4 Apr, 2020", "30 Jul, 2020")
    df = pd.DataFrame(klines)
    #print(df.head(1))
    if len(quotes) == 0:
        quotes['Date'] = df[0]
        quotes[s] = pd.to_numeric(df[4])
    else:
        new_df = pd.DataFrame()
        new_df['Date'] = df[0]
        new_df[s] = pd.to_numeric(df[4])
        quotes = quotes.merge(new_df, how="inner", on="Date")
    #print(quotes)
#print(quotes.tail(20))

XRPBTC


In [1149]:
info = client.get_account()
balances = info['balances']
print(round(10 / 9065, 4))
try:
   # order = client.create_order(
    #    symbol='BTCUSDT',
    #    side=Client.SIDE_BUY,
    #    type=Client.ORDER_TYPE_LIMIT,
    #    timeInForce=Client.TIME_IN_FORCE_GTC,
     #   quantity=round(20 / 9065, 4),
     #   price='9065')
    
   # print(order)

except BinanceAPIException as e:
    print(e.status_code)
    print(e.message)



IndentationError: expected an indented block (<ipython-input-1149-ad837b5753d3>, line 15)

In [1150]:
existing = client.get_all_orders(symbol='BTCUSDT', limit=10)
print(existing)

[{'symbol': 'BTCUSDT', 'orderId': 2619155254, 'orderListId': -1, 'clientOrderId': 'web_a086fb4d9cd74f3fbb69b91aa3a873c5', 'price': '9169.99000000', 'origQty': '0.00819700', 'executedQty': '0.00819700', 'cummulativeQuoteQty': '75.16640803', 'status': 'FILLED', 'timeInForce': 'GTC', 'type': 'LIMIT', 'side': 'SELL', 'stopPrice': '0.00000000', 'icebergQty': '0.00000000', 'time': 1593886033543, 'updateTime': 1593886449986, 'isWorking': True, 'origQuoteOrderQty': '0.00000000'}, {'symbol': 'BTCUSDT', 'orderId': 2620021812, 'orderListId': -1, 'clientOrderId': 'QqQbKHg7EVVPZIorTCsPSX', 'price': '9065.00000000', 'origQty': '0.00220000', 'executedQty': '0.00000000', 'cummulativeQuoteQty': '0.00000000', 'status': 'EXPIRED', 'timeInForce': 'FOK', 'type': 'LIMIT', 'side': 'BUY', 'stopPrice': '0.00000000', 'icebergQty': '0.00000000', 'time': 1593895850856, 'updateTime': 1593895850856, 'isWorking': True, 'origQuoteOrderQty': '0.00000000'}, {'symbol': 'BTCUSDT', 'orderId': 2620027116, 'orderListId': -1

In [1151]:
quotes['Date'] = pd.to_datetime(quotes['Date'], unit='ms')
quotes.set_index('Date', inplace=True)
print(quotes)

                       XRPBTC
Date                         
2020-04-04 00:00:00  0.000026
2020-04-04 00:30:00  0.000026
2020-04-04 01:00:00  0.000026
2020-04-04 01:30:00  0.000026
2020-04-04 02:00:00  0.000027
2020-04-04 02:30:00  0.000027
2020-04-04 03:00:00  0.000027
2020-04-04 03:30:00  0.000027
2020-04-04 04:00:00  0.000027
2020-04-04 04:30:00  0.000027
2020-04-04 05:00:00  0.000027
2020-04-04 05:30:00  0.000027
2020-04-04 06:00:00  0.000027
2020-04-04 06:30:00  0.000027
2020-04-04 07:00:00  0.000027
2020-04-04 07:30:00  0.000027
2020-04-04 08:00:00  0.000027
2020-04-04 08:30:00  0.000027
2020-04-04 09:00:00  0.000027
2020-04-04 09:30:00  0.000026
2020-04-04 10:00:00  0.000026
2020-04-04 10:30:00  0.000026
2020-04-04 11:00:00  0.000026
2020-04-04 11:30:00  0.000027
2020-04-04 12:00:00  0.000027
2020-04-04 12:30:00  0.000027
2020-04-04 13:00:00  0.000027
2020-04-04 13:30:00  0.000027
2020-04-04 14:00:00  0.000027
2020-04-04 14:30:00  0.000027
...                       ...
2020-07-04

In [1152]:
filtered = quotes#[quotes.index >= '2020-07-01']
filtered = filtered * 100000
normalized = filtered / filtered.iloc[0]
normalized.dropna(inplace=True)

In [1153]:
fig = go.Figure()
for c in normalized.columns:
    fig.add_trace(go.Scatter(x=normalized.index, y=normalized[c],
                    mode='lines',
                    name= c))

fig.show()

# Are they mean reverting?

In [1154]:
## Find most stationary instrument
for c in normalized.columns:
    ts = normalized[c]
    result = adfuller(ts)
    print(c)
    print(result)

XRPBTC
(-0.8238731413098389, 0.8120087427041822, 4, 4424, {'1%': -3.431829000533984, '5%': -2.8621935395791693, '10%': -2.5671178831251695}, -39870.28999240341)


In [1155]:
def hurst(ts):
    """Returns the Hurst Exponent of the time series vector ts"""
    # Create the range of lag values
    lags = range(2, 100)

    # Calculate the array of the variances of the lagged differences
    tau = [sqrt(std(subtract(ts[lag:], ts[:-lag]))) for lag in lags]

    # Use a linear fit to estimate the Hurst Exponent
    poly = polyfit(log(lags), log(tau), 1)

    # Return the Hurst exponent from the polyfit output
    return poly[0]*2.0

In [1156]:
## Find most stationary instrument
for c in normalized.columns:
    ts = normalized[c]
    result = hurst(ts)
    print(c)
    print(result)

XRPBTC
0.5019315299952485


# Tracing some indicators

In [1157]:
def get_bollinger_bands(window, no_of_std, ts):
    #Calculate rolling mean and standard deviation using number of days set above
    rolling_mean = ts.rolling(window).mean()
    rolling_std = ts.rolling(window).std()
    #create two new DataFrame columns to hold values of upper and lower Bollinger bands
    df = pd.DataFrame(columns=['mean', 'high', 'low'])
    df['mean'] = rolling_mean
    df['high'] = rolling_mean + (rolling_std * no_of_std)
    df['low'] = rolling_mean - (rolling_std * no_of_std)
    
    return df


In [1158]:
def get_mavgs(mavg_1, mavg_2, ts):
    m1 = base_fx.get_macd(ts, mavg_1)
    m2 = base_fx.get_macd(ts, mavg_2)
    return m1, m2

In [1233]:
symbol = 'XRPBTC'
bbands = get_bollinger_bands(100,.5, filtered[symbol])
m1, m2 = get_mavgs(5,15, filtered[symbol])

pairs_portfolio_fx.plot_objects([
    {'label': 'ts', 'value': filtered[symbol]},
    {'label': 'mean', 'value': bbands['mean']},
    {'label': 'high', 'value': bbands['high']},
    {'label': 'low', 'value': bbands['low']},
    {'label': 'm1', 'value': m1},
    {'label': 'm2', 'value': m2}
])

In [1234]:
portfolio['history']

symbol  type      amount  bought_at           bought_on status  \
0   XRPBTC   BUY  100.000000      2.636 2020-04-06 08:00:00  CLOSE   
1   XRPBTC  SELL  100.330677      2.688 2020-04-06 23:00:00  CLOSE   
2   XRPBTC  SELL   99.708313      2.701 2020-04-07 03:00:00  CLOSE   
3   XRPBTC   BUY   99.265329      2.714 2020-04-14 16:30:00  CLOSE   
4   XRPBTC   BUY   98.910037      2.709 2020-04-14 23:00:00  CLOSE   
5   XRPBTC   BUY   99.979499      2.697 2020-04-16 09:00:00  CLOSE   
6   XRPBTC   BUY   99.805378      2.697 2020-04-16 14:30:00  CLOSE   
7   XRPBTC   BUY   99.557549      2.671 2020-04-17 08:00:00  CLOSE   
8   XRPBTC   BUY   98.936162      2.669 2020-04-17 13:00:00  CLOSE   
9   XRPBTC   BUY   99.541530      2.671 2020-04-19 20:30:00  CLOSE   
10  XRPBTC   BUY   99.367453      2.663 2020-04-21 00:30:00  CLOSE   
11  XRPBTC   BUY   99.827797      2.643 2020-04-23 03:30:00  CLOSE   
12  XRPBTC   BUY   99.765740      2.595 2020-04-24 07:00:00  CLOSE   
13  XRPBTC   BUY   99.627529      2.562 2020-04-26 16:30:00  CLOSE   
14  XRPBTC   BUY   99.411241      2.563 2020-04-27 02:00:00  CLOSE   
15  XRPBTC   BUY   99.428191      2.560 2020-04-27 06:00:00  CLOSE   
16  XRPBTC   BUY   99.251085      2.460 2020-04-30 15:30:00  CLOSE   
17  XRPBTC   BUY   99.474602      2.464 2020-04-30 17:00:00  CLOSE   
18  XRPBTC   BUY   98.365847      2.451 2020-04-30 23:30:00  CLOSE   
19  XRPBTC  SELL   98.650328      2.502 2020-05-02 22:00:00  CLOSE   
20  XRPBTC   BUY   99.833185      2.443 2020-05-04 07:30:00  CLOSE   
21  XRPBTC   BUY   99.365567      2.433 2020-05-05 12:30:00  CLOSE   
22  XRPBTC   BUY   99.143679      2.208 2020-05-08 04:00:00  CLOSE   
23  XRPBTC   BUY   98.820026      2.209 2020-05-13 19:00:00  CLOSE   
24  XRPBTC   BUY   98.229119      2.077 2020-05-17 20:30:00  CLOSE   
25  XRPBTC  SELL   97.891019      2.114 2020-05-20 22:00:00  CLOSE   
26  XRPBTC  SELL   97.608089      2.128 2020-05-21 16:00:00  CLOSE   
27  XRPBTC  SELL   97.098078      2.143 2020-05-22 03:00:00  CLOSE   
28  XRPBTC  SELL   96.865187      2.194 2020-05-22 14:00:00  CLOSE   
29  XRPBTC  SELL   96.636004      2.189 2020-05-22 22:30:00  CLOSE   
..     ...   ...         ...        ...                 ...    ...   
41  XRPBTC   BUY   98.881794      2.083 2020-06-08 18:30:00  CLOSE   
42  XRPBTC   BUY   98.735441      2.063 2020-06-10 02:00:00  CLOSE   
43  XRPBTC   BUY   98.684566      2.048 2020-06-11 04:30:00  CLOSE   
44  XRPBTC   BUY   98.826810      2.035 2020-06-12 02:00:00  CLOSE   
45  XRPBTC   BUY   98.630856      2.031 2020-06-14 07:30:00  CLOSE   
46  XRPBTC   BUY   98.435100      2.030 2020-06-14 13:00:00  CLOSE   
47  XRPBTC  SELL   98.335212      2.039 2020-06-16 01:30:00  CLOSE   
48  XRPBTC   BUY   99.203301      2.021 2020-06-18 23:30:00  CLOSE   
49  XRPBTC   BUY   99.202270      2.015 2020-06-19 17:30:00  CLOSE   
50  XRPBTC   BUY   99.053836      2.004 2020-06-21 07:30:00  CLOSE   
51  XRPBTC   BUY   98.905354      2.004 2020-06-21 13:00:00  CLOSE   
52  XRPBTC   BUY   98.707741      2.001 2020-06-21 22:00:00  CLOSE   
53  XRPBTC   BUY   98.609033      1.993 2020-06-22 13:30:00  CLOSE   
54  XRPBTC   BUY   98.114603      1.960 2020-06-23 05:30:00  CLOSE   
55  XRPBTC   BUY   97.916371      1.962 2020-06-23 07:00:00  CLOSE   
56  XRPBTC   BUY   97.568923      1.961 2020-06-23 08:00:00  CLOSE   
57  XRPBTC  SELL   97.373882      1.977 2020-06-25 12:30:00  CLOSE   
58  XRPBTC  SELL   97.128896      2.000 2020-06-26 18:00:00  CLOSE   
59  XRPBTC   BUY   97.226025      1.945 2020-06-29 02:00:00  CLOSE   
60  XRPBTC   BUY   96.978836      1.931 2020-06-30 08:00:00  CLOSE   
61  XRPBTC   BUY   96.932079      1.923 2020-06-30 19:30:00  CLOSE   
62  XRPBTC   BUY   96.734334      1.920 2020-07-01 03:00:00  CLOSE   
63  XRPBTC   BUY   96.536835      1.920 2020-07-01 09:30:00  CLOSE   
64  XRPBTC   BUY   96.339738      1.913 2020-07-01 23:00:00  CLOSE   
65  XRPBTC   BUY   96.142678      1.914 2020-07-02 01:00:00  CLOSE   
66  XRPBTC  SE

# Algo

In [1235]:
def get_settings():
    return {
        'symbol': symbol,
        'mavg_1' : 5 ,
        'mavg_2': 15,
        'bband_period': 100,
        'bband_std':1,
        'limit': 0,
        'leverage_limit': 0,
        'exit_limit': 1, ## 1 = exits on mean
        'max_leverage': 1,
        'fee': 0.001, #0.1%,
        'stop_loss': -2
       }

In [1236]:
importlib.reload(base_fx)
importlib.reload(portfolio_fx)
importlib.reload(algos)
settings = get_settings()
portfolio, indicators = algos.mean_reversion_bbands(settings, filtered)

In [1240]:
pairs_portfolio_fx.plot_objects([{'label': 'nav', 'value': portfolio['nav']['nav']}])

In [1238]:
pairs_portfolio_fx.plot_objects([
    {'label': 'ts', 'value': filtered[symbol]},
    {'label': 'high', 'value': indicators['bbands']['high']},
    {'label': 'mean', 'value': indicators['bbands']['mean']},
    {'label': 'low', 'value': indicators['bbands']['low']},
    {'label': 'mavg_fast', 'value': indicators['mavg_fast']},
    {'label': 'mavg_slow', 'value': indicators['mavg_slow']},
])


In [1239]:
portfolio['history']#[portfolio['history']['bought_on'] > '2020-04-29']


symbol  type      amount  bought_at           bought_on status  \
0   XRPBTC  SELL   99.900000      2.707 2020-04-07 04:30:00  CLOSE   
1   XRPBTC   BUY   99.420244      2.714 2020-04-14 16:30:00  CLOSE   
2   XRPBTC   BUY   99.027765      2.709 2020-04-14 23:30:00  CLOSE   
3   XRPBTC   BUY  100.098500      2.697 2020-04-16 09:00:00  CLOSE   
4   XRPBTC   BUY   99.812828      2.697 2020-04-16 14:30:00  CLOSE   
5   XRPBTC   BUY   99.564980      2.693 2020-04-16 21:00:00  CLOSE   
6   XRPBTC   BUY   99.317528      2.669 2020-04-17 09:30:00  CLOSE   
7   XRPBTC   BUY   98.771672      2.671 2020-04-19 20:30:00  CLOSE   
8   XRPBTC   BUY   98.598942      2.663 2020-04-21 04:30:00  CLOSE   
9   XRPBTC   BUY   99.055725      2.591 2020-04-23 21:00:00  CLOSE   
10  XRPBTC   BUY   98.803747      2.589 2020-04-24 14:30:00  CLOSE   
11  XRPBTC   BUY   98.399640      2.575 2020-04-25 21:30:00  CLOSE   
12  XRPBTC   BUY   98.301240      2.562 2020-04-26 16:30:00  CLOSE   
13  XRPBTC   BUY   98.087832      2.468 2020-04-30 18:00:00  CLOSE   
14  XRPBTC   BUY   96.837173      2.452 2020-05-01 00:00:00  CLOSE   
15  XRPBTC   BUY   96.937801      2.442 2020-05-04 08:00:00  CLOSE   
16  XRPBTC   BUY   98.349314      2.433 2020-05-05 12:30:00  CLOSE   
17  XRPBTC   BUY   98.089272      2.209 2020-05-08 02:30:00  CLOSE   
18  XRPBTC   BUY   97.946779      2.208 2020-05-08 04:00:00  CLOSE   
19  XRPBTC   BUY   97.227793      2.194 2020-05-08 13:30:00  CLOSE   
20  XRPBTC   BUY   96.332889      2.208 2020-05-13 18:30:00  CLOSE   
21  XRPBTC  SELL   94.876343      2.128 2020-05-16 23:00:00  CLOSE   
22  XRPBTC   BUY   95.010097      2.077 2020-05-17 20:30:00  CLOSE   
23  XRPBTC  SELL   94.591681      2.114 2020-05-20 22:00:00  CLOSE   
24  XRPBTC  SELL   94.318287      2.129 2020-05-21 17:00:00  CLOSE   
25  XRPBTC  SELL   93.869910      2.141 2020-05-22 00:00:00  CLOSE   
26  XRPBTC  SELL   93.469439      2.143 2020-05-22 03:00:00  CLOSE   
27  XRPBTC  SELL   93.332397      2.193 2020-05-22 15:00:00  CLOSE   
28  XRPBTC  SELL   93.239065      2.186 2020-05-22 23:30:00  CLOSE   
29  XRPBTC  SELL   93.529317      2.208 2020-05-25 14:30:00  CLOSE   
..     ...   ...         ...        ...                 ...    ...   
31  XRPBTC   BUY   93.169775      2.097 2020-05-28 18:30:00  CLOSE   
32  XRPBTC   BUY   92.721165      2.103 2020-05-29 05:00:00  CLOSE   
33  XRPBTC   BUY   92.540264      2.089 2020-06-02 08:30:00  CLOSE   
34  XRPBTC   BUY   94.219677      2.082 2020-06-04 23:00:00  CLOSE   
35  XRPBTC   BUY   94.215966      2.086 2020-06-05 06:30:00  CLOSE   
36  XRPBTC  SELL   94.388594      2.115 2020-06-07 17:30:00  CLOSE   
37  XRPBTC   BUY   95.950580      2.083 2020-06-08 15:30:00  CLOSE   
38  XRPBTC   BUY   95.808566      2.064 2020-06-10 03:00:00  CLOSE   
39  XRPBTC   BUY   95.712757      2.047 2020-06-11 05:30:00  CLOSE   
40  XRPBTC   BUY   95.944348      2.038 2020-06-12 02:30:00  CLOSE   
41  XRPBTC   BUY   95.613015      2.031 2020-06-14 07:30:00  CLOSE   
42  XRPBTC   BUY   95.517402      2.030 2020-06-14 13:00:00  CLOSE   
43  XRPBTC   BUY   95.515990      2.021 2020-06-18 23:30:00  CLOSE   
44  XRPBTC   BUY   95.325951      2.015 2020-06-19 18:30:00  CLOSE   
45  XRPBTC   BUY   95.277933      2.005 2020-06-21 08:00:00  CLOSE   
46  XRPBTC   BUY   94.992574      2.004 2020-06-21 13:00:00  CLOSE   
47  XRPBTC   BUY   94.850180      2.001 2020-06-21 22:30:00  CLOSE   
48  XRPBTC   BUY   94.802731      1.960 2020-06-23 05:30:00  CLOSE   
49  XRPBTC   BUY   94.804666      1.961 2020-06-23 12:30:00  CLOSE   
50  XRPBTC  SELL   94.470261      1.998 2020-06-26 21:00:00  CLOSE   
51  XRPBTC   BUY   94.517544      1.944 2020-06-29 02:30:00  CLOSE   
52  XRPBTC   BUY   94.325786      1.923 2020-06-30 20:30:00  CLOSE   
53  XRPBTC   BUY   94.035255      1.917 2020-07-01 04:00:00  CLOSE   
54  XRPBTC   BUY   93.990273      1.920 2020-07-01 09:30:00  CLOSE   
55  XRPBTC   BUY   93.798376      1.914 2020-07-01 22:30:00  CLOSE   
56  XRPBTC   B

In [1224]:
neg = portfolio['history'][portfolio['history']['return'] < 0]
pos = portfolio['history'][portfolio['history']['return'] > 0]
total = len(neg) + len(pos)

print(len(neg))
print(len(pos))

print(len(pos)/total * 100)

59
32
35.16483516483517
